# Analizaremos los factores de exito de IPO's 

In [2316]:
import pandas as pd
import numpy as np
import matplotlib as mpl
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
import random

In [2317]:
df = pd.read_csv("IPODataFull.csv", low_memory=False,encoding='unicode_escape')
df.head()

Symbol  DaysBetterThanSP  daysProfit daysProfitGrouped  exactDiffernce  \
0      A               122         249              200+             NaN   
1    AAC               131         262              200+           232.0   
2   AAOI               125         262              200+          6054.0   
3    AAP               128         261              200+             NaN   
4    AAT               123         127         100 - 149           181.0   

   Year  Month  Day  dayOfWeek  closeDay0  ...  usableCEOAge  usableCEOGender  \
0  1999     11   18          3    28.6358  ...         Blank            Blank   
1  2014     10    2          3    18.5000  ...       40 - 49             male   
2  2013      9   26          3     9.9600  ...         Blank            Blank   
3  2001     11   29          3    13.9000  ...         Blank            Blank   
4  2011      1   13          3    21.2500  ...         Blank            Blank   

   usablePresidentAge  usablePresidentGender  FoundingDateGrouped  \
0               Blank                  Blank          1951 - 2000   
1               Blank                  Blank       2011 - present   
2               Blank                  Blank          1951 - 2000   
3               Blank                  Blank          1901 - 1950   
4               Blank                  Blank          2001 - 2010   

   yearDifferenceGrouped  Profitable  Safe  HomeRunDay  HomeRun  
0                Unknown           1     0        77.0        1  
1                Unknown           1     1         NaN        0  
2                Unknown           1     0         NaN        0  
3                Unknown           1     0         NaN        0  
4                Unknown           0     0         NaN        0  

[5 rows x 1664 columns]

In [2318]:
df.shape

(3762, 1664)

In [2319]:
colnames = list(df.columns)
#colnames[1000:len(colnames)]

# Separamos el DF principal en dos partes:
# 1. 'main': variables no referentes a precios
# 2. 'prices': variables referentes precios

In [2320]:
close_day_0 = df.columns.get_loc('closeDay0')
name = df.columns.get_loc('Name')

print(close_day_0)

df_prices = df.iloc[:,close_day_0:name]

colname_symbol = (df.columns[df.columns.get_loc('Symbol')])

df_prices.insert(0, colname_symbol, df['Symbol'])
df_prices['HomeRunDay'] = df['HomeRunDay']
df_prices['HomeRun']=df['HomeRun']
#df_prices

9


In [2321]:
df_main = df.drop(df.columns[close_day_0:name], axis=1)
df_main = df_main.drop(df.columns[-2:], axis=1)
#df_main

In [2322]:
print(df_prices.shape)
print(df_main.shape)

(3762, 1313)
(3762, 352)


# Seleccion de Variables del "df_main"

In [2323]:
df_main_columns = df_main.columns

In [2324]:
main_variables = []
for col_name in df_main.columns: 
    main_variables.append(col_name)

In [2325]:
# Variables que idealmente quisieramos usar. Lamentablemente no todas tienen mas de 2000 datos
ideal_variables = ['Symbol', 'DaysBetterThanSP','daysProfit', 'Year', 'Month', 'Day', 'dayOfWeek', 'MarketCap', 'Sector', 'Industry',
                      'CEOAge','CEOGender', 'CEOInChargeDuringIPO','City','stateCountry', 'Revenue', 'netIncome',' lastFiscalYearGrowth ',
                      'employees','YearFounded','Total_revenuesYearBeforeIPO','Operating_incomeYearBeforeIPO', 'EBITDAYearBeforeIPO','Net_incomeYearBeforeIPO','Profitable','Net_cash_used_for_investing_activitiesYearBeforeIPO',
                      'Other_financing_activitiesYearBeforeIPO','Cash_and_cash_equivalentsYearBeforeIPO','Total_stockholders_equityYearBeforeIPO',
                      'Retained_earningsYearBeforeIPO','Common_stock_repurchasedYearBeforeIPO','Debt_repaymentYearBeforeIPO','Long-term_debt_repaymentYearBeforeIPO','Long-term_debt_issuedYearBeforeIPO','Long-term_debtYearBeforeIPO',
                      'Debt_issuedYearBeforeIPO','Debt_securitiesYearBeforeIPO','Short-term_debtYearBeforeIPO','LoansYearBeforeIPO','Net_loansYearBeforeIPO',
                       'Repurchases_of_treasury_stockYearBeforeIPO','Dividend_paidYearBeforeIPO','Market6MonthTrend','MarketYearTrend']
                      

In [2326]:
df_main_nrows = df_main.shape[0]
df_main_nrows

3762

In [2327]:
# Identificamos las variables con pocos datos
na_s = df_main[main_variables].isna().sum()

short_columns = []
for i in range(0, len(na_s)):
    if na_s[i] > (df_main_nrows - 2000):
        short_columns.append(na_s.index[i])
        
#print(short_columns)
print(len(short_columns))

303


In [2328]:
# Retiramos las variables con menos de 2000 datos, son 303 de 352
df_main_clean = df_main.drop(short_columns, axis=1)
df_main_clean.shape

(3762, 49)

In [2329]:
# Visualizamos las variables restantes y elegimos las que mejor podrian explicar el valor de una IPO
df_main_clean.columns
selected_variables = ['Symbol','Name','DaysBetterThanSP', 'daysProfit','Year','Month','Day', 'dayOfWeek', 'LastSale', 'MarketCap', 'Sector',
       'Industry', 'Summary Quote','CEOTakeOver', 'CEOAge','CEOGender', 'CEOInChargeDuringIPO','City', 'stateCountry', 'FiscalDateEnd',
       'Revenue', 'netIncome', 'employees', 'YearFounded','Market6MonthTrend', 'MarketYearTrend', 'employeesGrouped',
       'USACompany', 'FiscalMonth','Profitable', 'Safe']

In [2330]:
df_main_clean = df_main_clean[selected_variables]

In [2331]:
df_main_clean['MarketYearTrend'] = round(df_main_clean['MarketYearTrend']/100, 4)

# Encontramos caracteristicas del DF 'prices'
## 1. Reemplazamos los nan

In [2332]:
df_prices.head()

Symbol  closeDay0  highDay0  openDay0  lowDay0  volumeDay0  closeDay1  \
0      A    28.6358   33.5207   27.3725  30.6572  59753154.0    27.2040   
1    AAC    18.5000   20.1000   17.6000  20.0000   2799073.0    18.6500   
2   AAOI     9.9600   10.0900    9.3700  10.0000    948999.0    10.1000   
3    AAP    13.9000   14.4667   13.3833  13.4000    371100.0    14.2834   
4    AAT    21.2500   22.0000   21.1800  21.5300  15536889.0    21.3100   

   highDay1  openDay1  lowDay1  ...  openDay260  lowDay260  volumeDay260  \
0   28.9727   26.8253  28.9323  ...     27.7936    28.9323     2944860.0   
1   18.7500   18.0500  18.2000  ...     22.1100    22.2700      197468.0   
2   10.4400   10.0000  10.4400  ...     16.9100    17.7300      177655.0   
3   14.2834   13.9000  13.9000  ...     16.7000    16.7000           0.0   
4   21.4500   21.1600  21.1600  ...     20.0900    20.8000      142910.0   

   closeDay261  highDay261  openDay261  lowDay261  volumeDay261  HomeRunDay  \
0      31.9205     31.9629     29.6465    29.6465     8351788.0        77.0   
1      24.4300     24.4800     22.4200    22.4200      295123.0         NaN   
2      16.8100     17.1000     16.5700    16.9300      230281.0         NaN   
3      17.1830     17.5500     17.0000    17.4300      553200.0         NaN   
4      20.6900     20.7100     20.2000    20.2000       87872.0         NaN   

   HomeRun  
0        1  
1        0  
2        0  
3        0  
4        0  

[5 rows x 1313 columns]

In [2333]:
# Para reemplazar los nan con valores de dias anteriores es necesario que sean de la misma medicion
df_closeDay_prices = df_prices.loc[:, df_prices.columns.str.contains('closeDay')]
df_highDay_prices = df_prices.loc[:, df_prices.columns.str.contains('highDay')]
df_openDay_prices = df_prices.loc[:, df_prices.columns.str.contains('openDay')]
df_lowDay_prices = df_prices.loc[:, df_prices.columns.str.contains('lowDay')]
df_volumeDay_prices = df_prices.loc[:, df_prices.columns.str.contains('volumeDay')]

In [2334]:
# Convertimos los DF en Arrays para reemplazar mas facilmente el 'nan' por el valor anterior

array_close_prices = df_closeDay_prices.to_numpy()
array_high_prices = df_highDay_prices.to_numpy()
array_open_prices = df_openDay_prices.to_numpy()
array_low_prices = df_lowDay_prices.to_numpy()
array_volume_prices = df_volumeDay_prices.to_numpy()


def nan_replacer(num_array):
    nan_location_array = np.where(np.isnan(num_array))
    counter_row = -1
    for i in num_array:
        counter_row += 1
        if counter_row in nan_location_array[0]:
            counter_col = -1

            for j in i:
                counter_col += 1
                if np.isnan(j):
                    num_array[counter_row, counter_col] = num_array[counter_row -1, counter_col-1]

In [2335]:
nan_replacer(array_close_prices)
nan_replacer(array_low_prices)
nan_replacer(array_open_prices)
nan_replacer(array_low_prices)
nan_replacer(array_volume_prices)

## 2. Insertamos la Media, Mediana y Desviacion Estandar en los DF

In [2336]:
# Convertimos los arrays sin nan's en DF para efectuar los calculos

df_closeDay_prices_clean = pd.DataFrame(array_close_prices, columns=df_closeDay_prices.columns)
df_highDay_prices_clean = pd.DataFrame(array_high_prices, columns=df_highDay_prices.columns)
df_openDay_prices_clean = pd.DataFrame(array_open_prices, columns=df_openDay_prices.columns)
df_lowDay_prices_clean = pd.DataFrame(array_low_prices, columns=df_lowDay_prices.columns)
df_volumeDay_prices_clean = pd.DataFrame(array_volume_prices, columns=df_volumeDay_prices.columns)

In [2337]:
def statistical_characteristics(df_day_prices_clean):
    df_day_prices_clean["Mean"] = df_day_prices_clean.mean(axis = 1)
    df_day_prices_clean["Median"] = df_day_prices_clean.median(axis = 1)
    df_day_prices_clean["Stan Dev."] = df_day_prices_clean.std(axis = 1)
    df_day_prices_clean["Symbol"] = df_main_clean["Symbol"]
    first_column = df_day_prices_clean.pop('Symbol')
    df_day_prices_clean.insert(0, 'Symbol', first_column)

In [2338]:
statistical_characteristics(df_closeDay_prices_clean)
statistical_characteristics(df_highDay_prices_clean)
statistical_characteristics(df_openDay_prices_clean)
statistical_characteristics(df_lowDay_prices_clean)
statistical_characteristics(df_volumeDay_prices_clean)

## 3.Visualizamos Variables del Main

In [2339]:
df_revenue_netIncome = pd.DataFrame()
df_revenue_netIncome["Symbol"] = df_main_clean["Symbol"]
df_revenue_netIncome["Sector"] = df_main_clean["Sector"]
df_revenue_netIncome["netIncome"] = df_main_clean["netIncome"]
df_revenue_netIncome["Revenue"] = df_main_clean["Revenue"]
df_revenue_netIncome["MarketCap"] = df_main_clean["MarketCap"]
df_revenue_netIncome = df_revenue_netIncome.dropna()

In [2340]:
df_main_clean.columns

Index(['Symbol', 'Name', 'DaysBetterThanSP', 'daysProfit', 'Year', 'Month',
       'Day', 'dayOfWeek', 'LastSale', 'MarketCap', 'Sector', 'Industry',
       'Summary Quote', 'CEOTakeOver', 'CEOAge', 'CEOGender',
       'CEOInChargeDuringIPO', 'City', 'stateCountry', 'FiscalDateEnd',
       'Revenue', 'netIncome', 'employees', 'YearFounded', 'Market6MonthTrend',
       'MarketYearTrend', 'employeesGrouped', 'USACompany', 'FiscalMonth',
       'Profitable', 'Safe'],
      dtype='object')

## 4. Desafio #3: Planteamiento de Preguntas de Interes/Hipotesis

 Hipotesis/Preguntas de interés - Totalidad (Pre-selección)

## Market Trend vs Fluctuacion del Precio
##### 4.1. ¿Qué sectores lo hacen mejor en los años alcistas?
##### 4.2. ¿Qué sectores lo hacen mejor en los años bajistas?
##### 4.3. ¿Cuál es la proporción de empresas que salen a cotizar en años bajistas vs alcistas?
##### 4.4. Las empresas de los diferentes sectores se distribuirán de forma normal en cuanto a crecimiento de la valorización se refiere.


## Ubicacion Geografica
##### 4.5 ¿Las empresas de cuáles países se desempeñan mejor por sector? Incluir un estudio de EEUU vs Resto del mundo

## Empleados
##### 4.6 ¿La cantidad de empleados se relaciona con el Market Cap? Diferenciar por sector

## Valoracion por Rentabilidad Futura
##### 4.7 ¿Hay relación entre si una empresa es rentable (profitable) en su primer año de cotización y su valoración? Existen muchos casos donde empresas sin resultados aumentan su valoración debido a promesas de resultados futuros, sobre todo las tecnológicas.

## Longevidad de la Empresa
##### 4.8 Una empresa antigua tenderá a hacerlo mejor en su primer año de cotización en mercados públicos?  Diferenciar por sector

## Volatilidad
##### 4.9 ¿Cómo se distribuye la capitalización de mercado de las IPO's? 
##### 4.10¿La capitalización de mercado está inversamente relacionada con la variación de la cotización y la volatilidad? Diferenciar por sector
##### 4.11 ¿Mayor volatilidad tiende a tener mayores retornos? Diferenciar por sector
##### 4.12 ¿Hay relación entre el volumen diario de una acción y su fluctuación diaria (high vs low)?

## Ratios financieros: P/E to growth
##### 4.13 ¿Cuál es la relación entre el P/E del año anterior a cotizar con la cotización en el primer año en bolsa? Diferenciar por sector

# ---------------------------------------------------------------------------------------------------------------

## Hipotésis Seleccionadas

##### 4.4. Las empresas de los diferentes sectores se distribuirán de forma normal en cuanto a crecimiento de la valorización se refiere.
##### 4.5. ¿Las empresas de cuáles países se desempeñan mejor por sector? Incluir un estudio de EEUU vs Resto del mundo
##### 4.6. ¿La cantidad de empleados se relaciona con el Market Cap? Diferenciar por sector
##### 4.8. Una empresa antigua tenderá a hacerlo mejor en su primer año de cotización en mercados públicos?  Diferenciar por sector
##### 4.9. ¿Cómo se distribuye la capitalización de mercado de las IPO's? 
##### 4.13. ¿Cuál es la relación entre el P/E del año anterior a cotizar con la cotización en el primer año en bolsa? Diferenciar por sector

# ---------------------------------------------------------------------------------------------------------------

## 5. Desafio #3: Visualizacion e Interpretacion de Graficos

## Market Trend vs Fluctuacion del Precio
##### 4.4. Las empresas de los diferentes sectores se distribuirán de forma normal en cuanto a crecimiento de la valorización se refiere.

In [2341]:
df_MarketYearTrend = df_main_clean[['Symbol','Sector','netIncome', 'MarketCap', 'MarketYearTrend']]
df_MarketYearTrend2 = pd.merge(df_MarketYearTrend, df_closeDay_prices_clean, on=['Symbol'], how='inner')
df_MarketYearTrend2.drop(df_MarketYearTrend2.iloc[:,5:-4], axis=1, inplace=True)
df_MarketYearTrend2 = df_MarketYearTrend2.drop_duplicates(subset='Symbol')
df_MarketYearTrend2.shape

(3699, 9)

In [2342]:
df_closeDay_prices_clean["Year_Price_Variation"] = (df_closeDay_prices_clean['closeDay261'] - df_closeDay_prices_clean['closeDay0'])/df_closeDay_prices_clean['closeDay0']

df = df_main_clean[['Symbol','Sector','netIncome', 'MarketCap', 'Year', 'YearFounded', 'MarketYearTrend']]
df_MarketYearTrend3 = pd.merge(df, df_closeDay_prices_clean, on=['Symbol'], how='inner')
df_MarketYearTrend3.drop(df_MarketYearTrend3.iloc[:,4:5], axis=1, inplace=True)
df_MarketYearTrend3.drop(df_MarketYearTrend3.iloc[:,6:-4], axis=1, inplace=True)
df_MarketYearTrend3 = df_MarketYearTrend3.drop_duplicates(subset='Symbol')

In [2343]:
df_MarketYearTrend3.head()

Symbol             Sector netIncome     MarketCap  YearFounded  \
0      A      Capital Goods  $684.00M  2.198323e+10       1999.0   
1    AAC        Health Care  $-20.58M  2.707691e+08       2014.0   
2   AAOI         Technology   $73.95M  5.844368e+08       1997.0   
3    AAP  Consumer Services  $475.51M  7.874971e+09       1929.0   
4    AAT  Consumer Services   $29.08M  1.604956e+09       2010.0   

   MarketYearTrend       Mean   Median  Stan Dev.  Year_Price_Variation  
0           0.0204  46.378060  44.8908  16.334874              0.114706  
1           0.0088  30.168664  29.5400   7.078500              0.320541  
2           0.0144  18.051160  18.4200   4.599134              0.687751  
3          -0.0075  16.715145  16.7000   1.840810              0.236187  
4           0.0226  20.724008  21.1500   1.295989             -0.026353

In [2344]:
df_MarketYearTrend3.Sector = df_MarketYearTrend3.Sector.fillna('No Specific Sector')

df_MarketYearTrend3.head()

# Eliminar compañias con variaciones mayores al 1000% (se multiplica 10x su cotización en bolsa el primer año).
index_year_price_change = df_MarketYearTrend3[(df_MarketYearTrend3['Year_Price_Variation'] >= 10)].index
df_MarketYearTrend3.drop(index_year_price_change , inplace=True)
df_MarketYearTrend3.shape

(3633, 10)

In [2345]:
fig = make_subplots(rows=7, cols=2, subplot_titles=df_MarketYearTrend5.Sector.unique())
fig.update_layout(autosize=False, width=800,height=1800, showlegend=False)
xs = []
counterx = 1
countery = 1
count = 1
for i in df_MarketYearTrend5.Sector.unique():    
    df = df_MarketYearTrend5[df_MarketYearTrend5['Sector']==i]
    xs.append(df['Year_Price_Variation'])
    Sector = go.Histogram(x=xs[count-1])
    fig.append_trace(Sector, counterx, countery)
    
    if count%2 == 0:
        counterx += 1
    else:
        countery += 1
        
    if count %2 ==0:
        countery = 1
    count += 1

fig.show()

##### Vemos que de las 13 distribuciones, la que tiene una forma marcádamente diferente al resto es la de Consumer Durables (consumo discrecional). Por lo general es un sector que es muy sensible al momento macroeconómico general. El resto de distribuciones parecen ser de forma aproximadamente 'normal' sobre todo si se les acota más en cuanto al crecimiento anual (hasta 200% o 2x). De cualquier forma, sería importante realizar un test de normalidad para validar esta conclusión.

##### 4.5. ¿Las empresas de cuáles países se desempeñan mejor por sector? Incluir un estudio de EEUU vs Resto del mundo

In [2346]:
df_MarketYearTrend5.columns

Index(['Symbol', 'Sector', 'netIncome', 'MarketCap', 'YearFounded',
       'MarketYearTrend', 'Mean', 'Median', 'Stan Dev.',
       'Year_Price_Variation', 'MC_discrete_classifier', 'stateCountry',
       'USACompany'],
      dtype='object')

In [2347]:
df_MarketYearTrend4.columns

Index(['Symbol', 'Sector', 'netIncome', 'MarketCap', 'YearFounded',
       'MarketYearTrend', 'Mean', 'Median', 'Stan Dev.',
       'Year_Price_Variation', 'MC_discrete_classifier'],
      dtype='object')

In [2348]:
df = df_main_clean[['Symbol', 'stateCountry', 'USACompany']]
df_MarketYearTrend5 = pd.merge(df_MarketYearTrend4, df, on=['Symbol'], how='inner')

In [2349]:
df = df_MarketYearTrend5
fig = px.histogram(df, x="Year_Price_Variation", color="USACompany")
fig.show()

##### El histograma apilado muestra la proporción de empresas de EEUU vs Resto del Mundo vs Origen desconocido y se ve la clara preponderancia de las empresas del país norteamericano pero pareciera que se distribuyen de igual manera en relación al tamaño sin importar el origen.  

##### A continuación mostraremos las distribuciones en conjunto y luego por separado para mayor claridad y además las proporciones exactas del lugar de origen de las empresas:

In [2350]:
group_labels = df_MarketYearTrend5.USACompany.unique()
df = df_MarketYearTrend5[df_MarketYearTrend5['USACompany']== group_labels[0]]
df2 = df_MarketYearTrend5[df_MarketYearTrend5['USACompany']== group_labels[1]]
df3 = df_MarketYearTrend5[df_MarketYearTrend5['USACompany']== group_labels[2]]

hist_data = [df["Year_Price_Variation"], df2["Year_Price_Variation"], df3["Year_Price_Variation"]]
fig = ff.create_distplot(hist_data, group_labels, show_hist=False, show_curve=True, curve_type='normal')
fig.update_layout(xaxis_range=[-1,2], bargap=0.01)

fig.show()


print("\033[1m"+"Media, Mediana y Desviacion Estandar por lugar de origen"+"\033[0m")
print("EEUU: ", round(df['Year_Price_Variation'].mean(),2), round(df['Year_Price_Variation'].median(),2), round(df['Year_Price_Variation'].std(), 2))
print("Extranjeras: ", round(df2['Year_Price_Variation'].mean(),2), round(df2['Year_Price_Variation'].median(),2), round(df2['Year_Price_Variation'].std(), 2))
print("Origen Desconocido: ",round(df3['Year_Price_Variation'].mean(),2), round(df3['Year_Price_Variation'].median(),2), round(df3['Year_Price_Variation'].std(), 2))



Media, Mediana y Desviacion Estandar por lugar de origen
EEUU:  0.27 0.04 1.16
Extranjeras:  0.35 0.03 1.3
Origen Desconocido:  0.13 -0.01 0.87


##### En los tres casos de lugar de origen, el crecimiento medio es muy optimista (mayor al 10%, cuando el S&P crece al 10%). Sin embargo, la mediana muestra la verdadera cara de invertir en empresas que recién salen a cotizar: muchas de ellas no obtienen una buena adopción en el mercado en su primer año. En cuanto a desviación estándar se refiere, las empresas de origen desconocido son las más predecibles, pero recordemos que son las que peores resultados de media y mediana obtuvieron.

In [2351]:
df_MarketYearTrend5.USACompany.value_counts()

Yes        2269
Unknown     866
No          561
Name: USACompany, dtype: int64

##### 61.4% de las compañías del DF son de origen estadounidense, mientras que 23.4% son extranjeras y el restante 15.2% son de origen desconocido.

In [2352]:
fig = make_subplots(rows=3, cols=1, subplot_titles=df_MarketYearTrend5.USACompany.unique(), shared_xaxes=True)
fig.update_layout(autosize=False, width=800,height=1000, showlegend=False, xaxis_range=[-1,2])
xs = []
count = 1
for i in df_MarketYearTrend5.USACompany.unique():    
    df = df_MarketYearTrend5[df_MarketYearTrend5['USACompany']==i]
    xs.append(df['Year_Price_Variation'])
    USACompany = go.Histogram(x=xs[count-1])
    fig.append_trace(USACompany, count, 1)
    count += 1

    
fig['layout']['xaxis']['title']='First Year Growth'
fig['layout']['yaxis']['title']='Number of Companies'
fig['layout']['xaxis2']['title']='First Year Growth'
fig['layout']['yaxis2']['title']='Number of Companies'
fig['layout']['xaxis3']['title']='First Year Growth'
fig['layout']['yaxis3']['title']='Number of Companies'

fig.show()

##### Según los histogramas podemos ver que las distribuciones de las compañías americanas son similares a las de origen desconocido. Quizás muchas de las de origen desconocido sean efectivamente americanas.

##### En el siguiente box plot veremos como se distribuye la variacion de precios por sector separado por lugar de origen.

In [2353]:
df = df_MarketYearTrend5
fig = px.box(df, x="Sector", y="Year_Price_Variation", color="USACompany")
fig.update_traces(quartilemethod="exclusive") # or "inclusive", or "linear" by default
fig.show()

##### El boxplot por sector permite percatarnos de que existen muchos 'outliers' en la mayoría de grupos divididos por lugar de origen y sector. Sin embargo, destaca el boxplot de empresas extranjeras de 'No Specific Sector'  debido a sus dimensiones. Esta forma extraña podría deberse a una baja cantidad de datos de dicho grupo. A continuación mostraremos una tabla con los datos divididos por sector y comprobaremos esta hipótesis.

In [2354]:
df_MarketYearTrend5.USACompany.value_counts()

df = df_MarketYearTrend5[df_MarketYearTrend5['USACompany']=='Yes']
df2 = df_MarketYearTrend5[df_MarketYearTrend5['USACompany']=='No']
df3 = df_MarketYearTrend5[df_MarketYearTrend5['USACompany']=='Unknown']

df =  df.groupby("Sector").count()
df2 = df2.groupby("Sector").count()
df3 = df3.groupby("Sector").count()

df =  df.sort_values('Symbol', ascending=False).reset_index()
df.drop(axis=1,columns=df.columns[2:], inplace=True)

df2 =  df2.sort_values('Symbol', ascending=False).reset_index()
df2.drop(axis=1,columns=df2.columns[2:], inplace=True)

df3 =  df3.sort_values('Symbol', ascending=False).reset_index()
df3.drop(axis=1,columns=df3.columns[2:], inplace=True)

df.rename(columns={"Symbol":"USA"}, inplace=True)
df2.rename(columns={"Symbol":"Foreign"}, inplace=True)
df3.rename(columns={"Symbol":"Unknown"}, inplace=True)


df = pd.merge(df, df2, on=['Sector'], how='inner')
df = pd.merge(df, df3, on=['Sector'], how='inner')

df['Total'] = df['USA'] + df['Foreign'] + df['Unknown']

df.sort_values('Total', ascending=False, inplace=True)
df = df.reset_index()
df.drop(['index'], axis=1, inplace=True)
df

Sector  USA  Foreign  Unknown  Total
0      No Specific Sector  111        8      594    713
1                 Finance  422       78       79    579
2             Health Care  423       91       40    554
3       Consumer Services  404       60       46    510
4              Technology  277       98       30    405
5                  Energy  132       33       10    175
6           Capital Goods  113       33        8    154
7        Basic Industries   89       43       12    144
8        Public Utilities   78       29       15    122
9           Miscellaneous   77       19        8    104
10  Consumer Non-Durables   68       26        8    102
11         Transportation   29       36       10     75
12      Consumer Durables   46        7        6     59

##### Como se ve en la tabla, efectivamente, la categría extranjeras de 'No Specific Sector' cuenta con tan solo 8 datos. Esta tabla permite mostrar sobre cuáles subgrupos se pueden hacer análisis importantes y sobre cuales no es profesional hacerlo debido a la falta de datos.

##### 4.6. ¿La cantidad de empleados se relaciona con el Market Cap? Diferenciar por sector

In [2355]:
df_MarketYearTrend6 = df_MarketYearTrend5

In [2356]:
df = df_main_clean[['Symbol', 'employees', 'employeesGrouped']]
df_MarketYearTrend6 = pd.merge(df_MarketYearTrend4, df, on=['Symbol'], how='inner')

In [2357]:
df_MarketYearTrend6.employeesGrouped.unique()

array(['>10000', '1001 - 5000', '101 - 500', '0 - 100', nan, '501 - 1000',
       'Blank', '5001 - 10000'], dtype=object)

In [2358]:
df_MarketYearTrend6['employees'] = pd.to_numeric(df_MarketYearTrend6['employees'], errors='coerce')

In [2359]:
df_MarketYearTrend6.shape

(3696, 13)

In [2360]:
bins = pd.IntervalIndex.from_tuples([(0, 100), (101, 500), (501, 1000), (1001, 5000), (5001, 10000), (10000, max(df_MarketYearTrend6.employees))], closed='left')
catDf = pd.cut(df_MarketYearTrend4["MarketCap"], bins = bins)
maximus_E = max(df_MarketYearTrend6.employees)
a = ('0 - 100', '101 - 500', '501 - 1000', '1001 - 5000', '5001 - 10000', f'10000 - {maximus_E}')


df_MarketYearTrend6['employeesGrouped'] = np.array(a)[pd.cut(df_MarketYearTrend6["employees"], bins = bins).cat.codes]

In [2361]:
bins = pd.IntervalIndex.from_tuples([(0, 1000000000), (1000000000, 5000000000), (5000000000, 10000000000), (10000000000, 100000000000), (100000000000, 1000000000000)], closed='left')
catDf = pd.cut(df_MarketYearTrend6["MarketCap"], bins = bins)
maximus_MC = round(max(df_MarketYearTrend6.MarketCap)/1000000000)
a = ('0 - 1B', '1B - 5B', '5B - 10B', '10B - 100B', f'100B - {maximus_MC}B')
df_MarketYearTrend6['MarketCapClassifier'] = np.array(a)[pd.cut(df_MarketYearTrend6["MarketCap"], bins = bins).cat.codes]

In [2362]:
df = df_MarketYearTrend6
fig = px.density_heatmap(df, x="MarketCapClassifier", y="employeesGrouped", marginal_x="histogram", text_auto=True)
fig.update_yaxes(categoryorder='array', categoryarray= ['0 - 100', '101 - 500', '501 - 1000', '1001 - 5000', '5001 - 10000', f'10000 - {maximus_E}'])
fig.update_xaxes(categoryorder='array', categoryarray= ['0 - 1B', '1B - 5B', '5B - 10B', '10B - 100B', f'100B - {maximus_MC}B'])
fig.show()

In [2363]:
df_MarketYearTrend6.shape

(3696, 14)

##### Como se ve en el gráfico de densidad 2D, 2297 empresas de 3696 (62%) no superan los mil millones (Billion) de capitalización de mercado en su primer año en bolsa. Este grupo además es el que concentra más empresas con el rango menor de empleados (0 a 100) lo cual tiene sentido. Sin embargo, su segundo rango más poblado es el máximo, lo cual es muy curioso. De hecho, este fenómeno ocurre en todas las capitalizaciones de mercado (el rango más  poblado es el de más empleados). Haciendo ver que no hay una relación tan clara entre tamaño o Market Cap y número de empleados. Sin embargo, sí podemos ver conforme nos movemos a la derecha del cuadro que si bien la relación mencionada no es tan fuerte, igual existe (ver la columna de mayor capitalización).

##### 4.8. Una empresa antigua tenderá a hacerlo mejor en su primer año de cotización en mercados públicos?  Diferenciar por sector

In [2364]:
df_MarketYearTrend6.columns

Index(['Symbol', 'Sector', 'netIncome', 'MarketCap', 'YearFounded',
       'MarketYearTrend', 'Mean', 'Median', 'Stan Dev.',
       'Year_Price_Variation', 'MC_discrete_classifier', 'employees',
       'employeesGrouped', 'MarketCapClassifier'],
      dtype='object')

In [2365]:
df_main_clean.columns

Index(['Symbol', 'Name', 'DaysBetterThanSP', 'daysProfit', 'Year', 'Month',
       'Day', 'dayOfWeek', 'LastSale', 'MarketCap', 'Sector', 'Industry',
       'Summary Quote', 'CEOTakeOver', 'CEOAge', 'CEOGender',
       'CEOInChargeDuringIPO', 'City', 'stateCountry', 'FiscalDateEnd',
       'Revenue', 'netIncome', 'employees', 'YearFounded', 'Market6MonthTrend',
       'MarketYearTrend', 'employeesGrouped', 'USACompany', 'FiscalMonth',
       'Profitable', 'Safe'],
      dtype='object')

In [2366]:
df_CompanyAge = df_MarketYearTrend6

In [2367]:
df = df_main_clean[['Symbol', 'Year']]
df_CompanyAge = pd.merge(df_CompanyAge, df, on=['Symbol'], how='inner')
df_CompanyAge.head()

Symbol             Sector netIncome     MarketCap  YearFounded  \
0      A      Capital Goods  $684.00M  2.198323e+10       1999.0   
1    AAC        Health Care  $-20.58M  2.707691e+08       2014.0   
2   AAOI         Technology   $73.95M  5.844368e+08       1997.0   
3    AAP  Consumer Services  $475.51M  7.874971e+09       1929.0   
4    AAT  Consumer Services   $29.08M  1.604956e+09       2010.0   

   MarketYearTrend       Mean   Median  Stan Dev.  Year_Price_Variation  \
0           0.0204  46.378060  44.8908  16.334874              0.114706   
1           0.0088  30.168664  29.5400   7.078500              0.320541   
2           0.0144  18.051160  18.4200   4.599134              0.687751   
3          -0.0075  16.715145  16.7000   1.840810              0.236187   
4           0.0226  20.724008  21.1500   1.295989             -0.026353   

   MC_discrete_classifier  employees  employeesGrouped MarketCapClassifier  \
0                       4    13500.0  10000 - 566000.0          10B - 100B   
1                       1     2100.0       1001 - 5000              0 - 1B   
2                       1     3054.0       1001 - 5000              0 - 1B   
3                       3    71000.0  10000 - 566000.0            5B - 10B   
4                       2      194.0         101 - 500             1B - 5B   

   Year  
0  1999  
1  2014  
2  2013  
3  2001  
4  2011

In [2368]:
df_CompanyAge['YearsBeforeIpo'] = df_CompanyAge['Year'] - df_CompanyAge['YearFounded']

In [2369]:
# eliminar compañías de más de 200 años de antiguedad (hay un dato de 2000 años)
index_year_price_change = df_CompanyAge[(df_CompanyAge['YearsBeforeIpo'] > 200)].index
df_CompanyAge.drop(index_year_price_change , inplace=True)

In [2370]:
df = df_CompanyAge
fig = px.scatter(df, x="YearsBeforeIpo", y="Year_Price_Variation", hover_data=['Symbol'], color="Sector", size='MC_discrete_classifier') 

fig.update_layout(yaxis_tickformat = '0%', xaxis_tickformat = '0')

fig.show()

##### Una empresa más antigua no lo hará necesariamente mejor en bolsa en su primer año de cotización, pero sí será más predecible el rango sobre el cual fluctuará el incremento en su valoración según el gráfico. Además, viendo el tamaño de las burbujas, parece que las empresas con mayor Market Cap suelen tener también un rango más acotado. Con estos dos hallazgos podemos suponer que si lo que se busca son rendimientos más predecibles pero menores, empresas grandes y con más edad son la mejor opción cuando salen a cotizar.

##### 4.9. ¿Cómo se distribuye la capitalización de mercado de las IPO's? 

In [2371]:
# Entendiendo las variaciones en el Market Cap
df = df_MarketYearTrend3
fig = px.histogram(df, x="MarketCap", color="Sector")
fig.show()

##### El histograma muestra una distribución sesgada a la derecha (concentración de datos cercana al eje Y) en cuanto a Market Cap se refiere. Es decir la mayoría de compañías que salen a IPO's no superan los 100 Billion (no billones, sino 'Billions', miles de millón en español).

##### El scatterplot a continuación muestra la relación entre la variable 'Year Price Variation' y 'Market Year Trend', pero además, el tamaño de los puntos indica el Market Cap. Como se ve, hay puntos que casi no figuran debido a lo diminutas que son muchas compañías frente a unas pocas que son muy grandes. Por esto deberemos hacer una ajuste y categorizar los tamaños para que todas las compañías puedan apreciarse en el gráfico.

In [2372]:
df = df_MarketYearTrend3
fig = px.scatter(df, x="MarketYearTrend", y="Year_Price_Variation", hover_data=['Mean'], color="Sector", size='MarketCap') 
fig.show()

In [2373]:
df_MarketYearTrend4 = df_MarketYearTrend3

bins = pd.IntervalIndex.from_tuples([(0, 1000000000), (1000000000, 5000000000), (5000000000, 10000000000), (10000000000, 100000000000), (100000000000, 1000000000000)], closed='left')
catDf = pd.cut(df_MarketYearTrend4["MarketCap"], bins = bins)
a = pd.to_numeric(list('123456'))
df_MarketYearTrend4['MC_discrete_classifier'] = np.array(a)[pd.cut(df_MarketYearTrend4["MarketCap"], bins = bins).cat.codes]

In [2374]:
df = df_MarketYearTrend3
fig = px.scatter(df, x="MarketYearTrend", y="Year_Price_Variation", hover_data=['Mean'], color="Sector", size='MC_discrete_classifier') 

fig.update_layout(yaxis_tickformat = '0%', xaxis_tickformat = '0%')

fig.show()

##### Para aclarar lo mostrado por el gráfico, medimos la correlación de las empresas con reciente IPO de cada sector contra la performance de la economía (S&P500). En el gráfico pareciera que la mayoría de empresas salen a cotizar después de un año bueno de bolsa, lo cual tiene sentido ya que la mayoría de años el S&P500 es positivo. Pero no se logra apreciar cómo afecta esto al rendimiento de la acción.

In [2375]:
df_MarketYearTrend4.groupby('Sector')[['MarketYearTrend','Year_Price_Variation']].corr().unstack().iloc[:,1]

Sector
Basic Industries        -0.114561
Capital Goods           -0.027747
Consumer Durables        0.195017
Consumer Non-Durables    0.058624
Consumer Services       -0.065598
Energy                   0.004819
Finance                 -0.018672
Health Care             -0.052601
Miscellaneous           -0.153203
No Specific Sector       0.032115
Public Utilities        -0.050494
Technology              -0.071549
Transportation           0.057985
Name: (MarketYearTrend, Year_Price_Variation), dtype: float64

##### Parece que ningún sector tiene una correlación siginifcativa con la performance del S&P 500, quizás deba deberse a que al ser IPO's los mercados parecen aceptarlas con muchas espectativas ya que tienen más espacio para crecer debido al salto abrupto en la facilidad de adquirir estas compañías una vez que son públicas versus cuando eran privadas.

##### Otra explicación pueda ser que un año bueno para el S&P no quiere decir un año bueno para el sector de una compañía en específico. Lo ideal sería analizar los sectores contra indicadores del mismo sector.

## Ratios financieros: P/E to growth
##### 4.13. ¿Cuál es la relación entre el P/E del año anterior a cotizar con la cotización en el primer año en bolsa? Diferenciar por sector

#### El P/E es un indicador del precio de una acción relativo al número de veces de esta sobre los EPS (ingresos netos por acción). Ya que indica el "número de veces" forma parte de los indicadores conocidos como "múltiplos". Generamente un P/E por debajo de la media indica que la empresa está subvaluada y por ende tiene más probabilidades de aumentar su cotización en el futuro.

#### Probaremos esta hipótesis diferenciada por sector (ya que influye en el P/E) y deberíamos esperar una correlación negativa entre el P/E del año antes de salir a cotizar con la variación del precio en bolsa.

In [2376]:
# Armamos un DF para calcular el P/E de cada empresa por sector
df_closeDay_prices_clean["Year_Price_Variation"] = (df_closeDay_prices_clean['closeDay261'] - df_closeDay_prices_clean['closeDay0'])/df_closeDay_prices_clean['closeDay0']
df_PE = df_main_clean[['Symbol','Sector','netIncome', 'MarketCap', 'Year', 'YearFounded']]
df_PE2 = pd.merge(df_PE, df_closeDay_prices_clean, on=['Symbol'], how='inner')
df_PE2.drop(df_PE2.iloc[:,4:-4], axis=1, inplace=True)
df_PE2 = df_PE2.drop_duplicates(subset='Symbol')

In [2377]:
# Eliminar compañias con variaciones mayores al 1000% (se multiplica 10x su cotización en bolsa el primer año).
index_year_price_change = df_PE2[(df_PE2['Year_Price_Variation'] >= 10)].index
df_PE2.drop(index_year_price_change , inplace=True)
df_PE2.shape

(3633, 8)

In [2378]:
print(df_PE.shape)
print(df_PE2.shape)
print(df_closeDay_prices_clean.shape)

(3762, 6)
(3633, 8)
(3762, 267)


In [2379]:
df_PE3 = df_PE2
df_PE3['netIncome'] = df_PE3['netIncome'].str[1:-1]
df_PE3.netIncome.value_counts(dropna=False)

NaN        870
105.85       4
5.94         4
-9.77        4
1.28         4
          ... 
-29.99       1
55.27        1
102.45       1
-277.19      1
-32.01       1
Name: netIncome, Length: 2475, dtype: int64

##### Vemos que existen 881 NaNs de un total de 3699 datos en la columna 'netIncome'. Estos datos deberan ser eliminados.

In [2380]:
df_PE3.dtypes

Symbol                   object
Sector                   object
netIncome                object
MarketCap               float64
Mean                    float64
Median                  float64
Stan Dev.               float64
Year_Price_Variation    float64
dtype: object

##### El tipo de dato de netIncome es un 'object', esto nos dará un error si lo intentamos usar para sacar el P/E ya que MarketCap es float. Deberemos corregir esto antes de realizar cualquier cálculo.

In [2381]:
df_PE3 = df_PE3.dropna()
df_PE3 = df_PE3.reset_index()

In [2382]:
df_PE3['netIncome'] = pd.to_numeric(df_PE3['netIncome'], errors='coerce')
df_PE3['netIncome'] = df_PE3['netIncome']*1000000
print(df_PE3.dtypes)

index                     int64
Symbol                   object
Sector                   object
netIncome               float64
MarketCap               float64
Mean                    float64
Median                  float64
Stan Dev.               float64
Year_Price_Variation    float64
dtype: object


In [2383]:
df_PE3['P/E'] = round(df_PE3['MarketCap']/df_PE3['netIncome'])

In [2384]:
df_PE3.groupby('Sector')[['P/E','Year_Price_Variation']].corr().unstack().iloc[:,1]

Sector
Basic Industries         0.039277
Capital Goods            0.049168
Consumer Durables       -0.108519
Consumer Non-Durables   -0.090785
Consumer Services        0.088855
Energy                  -0.025013
Finance                 -0.032669
Health Care             -0.012272
Miscellaneous           -0.210954
Public Utilities         0.103568
Technology               0.124359
Transportation          -0.048095
Name: (P/E, Year_Price_Variation), dtype: float64

#### Al parecer si bien la correlación es negativa para la mayoría de sectores vs el P/E del año anterior, estas son muy bajas y difícilmente serán siginificativas. Puede deberse a que quizás otras variables estén influyendo (como el país de origen o el momento en que salieron a cotizar). También podría no ser cierta la hipótesis para variación de precios de una IPO después de tan solo 1 año de cotizar públicamente.

In [2385]:
fig = make_subplots(rows=7, cols=2, subplot_titles=df_PE3.Sector.unique())
fig.update_layout(autosize=False, width=800,height=1800, showlegend=False)
xs = []
ys = []
counterx = 1
countery = 1
count = 1
for i in df_PE3.Sector.unique():    
    df = df_PE3[df_PE3['Sector']==i]
    xs.append(df['P/E'])
    ys.append(df['Year_Price_Variation'])

    Sector = go.Scatter(x=xs[count-1], y=ys[count-1], mode='markers')
    fig.append_trace(Sector, counterx, countery)
    
    if count%2 == 0:
        counterx += 1
    else:
        countery += 1
        
    if count %2 ==0:
        countery = 1
    count += 1

fig.show()

##### Usualmente la media del S&P para el P/E es 18, por lo que eliminaremos los datos mayores a 200 (rara vez se encuentran datos mayores a 100 y generalmente es una valoración insostenible en el tiempo. Tampoco se suele usar valores de multiplos negativos.

In [2386]:
# Eliminar compañias con valoraciones superiores a 200 o con multiplos menores a 0.
df_PE4 = df_PE3
index_PE = df_PE4[(df_PE4['P/E'] >= 200)].index
df_PE4.drop(index_PE , inplace=True)
index_PE = df_PE4[(df_PE4['P/E'] <= 0)].index
df_PE4.drop(index_PE , inplace=True)
df_PE4.reset_index(inplace=True)

In [2387]:
df_PE4.drop(['level_0','index'], axis=1)

Symbol             Sector    netIncome     MarketCap       Mean   Median  \
0         A      Capital Goods  684000000.0  2.198323e+10  46.378060  44.8908   
1      AAOI         Technology   73950000.0  5.844368e+08  18.051160  18.4200   
2       AAP  Consumer Services  475510000.0  7.874971e+09  16.715145  16.7000   
3       AAT  Consumer Services   29080000.0  1.604956e+09  20.724008  21.1500   
4       AAV             Energy   95040000.0  5.857840e+08   6.075099   6.0750   
...     ...                ...          ...           ...        ...      ...   
1277   ZNGA         Technology   26630000.0  3.080763e+09   6.708347   5.7650   
1278    ZTO     Transportation  467530000.0  1.127765e+10  13.925878  14.0100   
1279    ZTS        Health Care  864000000.0  4.094335e+10  31.803969  31.8100   
1280   ZUMZ  Consumer Services   26800000.0  6.085133e+08  20.266053  17.8850   
1281     ZX      Capital Goods    1340000.0  6.711250e+07   4.346186   4.2800   

      Stan Dev.  Year_Price_Variation    P/E  
0     16.334874              0.114706   32.0  
1      4.599134              0.687751    8.0  
2      1.840810              0.236187   17.0  
3      1.295989             -0.026353   55.0  
4      0.973293             -0.068069    6.0  
...         ...                   ...    ...  
1277   4.008748             -0.294737  116.0  
1278   1.084280             -0.050694   24.0  
1279   1.549225             -0.498871   47.0  
1280   5.938845              1.441496   23.0  
1281   0.842612             -0.408547   50.0  

[1282 rows x 9 columns]

In [2388]:
df_PE4.Year_Price_Variation.max()

9.166666666666668

In [2389]:
fig = make_subplots(rows=7, cols=2, subplot_titles=df_PE4.Sector.unique())
fig.update_layout(autosize=False, width=800,height=1800, showlegend=False)
xs = []
ys = []
counterx = 1
countery = 1
count = 1
for i in df_PE4.Sector.unique():    
    df = df_PE4[df_PE4['Sector']==i]
    xs.append(df['P/E'])
    ys.append(df['Year_Price_Variation'])

    Sector = go.Scatter(x=xs[count-1], y=ys[count-1], mode='markers')
    fig.append_trace(Sector, counterx, countery)
    
    if count%2 == 0:
        counterx += 1
    else:
        countery += 1
        
    if count %2 ==0:
        countery = 1
    count += 1

fig.show()

##### En Health Care, Technology, Energy y Miscellaneous parece comprobarse el efecto inverso del P/E sobre la variación del precio (a menor P/E, mayor potencial de revalorización). Sin embargo los resultados en general son decepcionantes en cuanto a esta hipótesis. Parece que en el caso de empresas que recién salen a cotizar, el P/E del año previo a salir a bolsa no parece ser muy relevante, puede deberse a que no hay un historial público como para determinar si la empresa está cara o barata respecto a su histórico y solo se le puede contrastar con el sector. Otra explicación es que la euforia de la salida a bolsa minimice el efecto de una valoración razonble basada en el múltiplo P/E. Finalmente, quizás este indicador sí tenga un peso significativo ya que hay sectores donde parece influir, pero no sea algo muy importante.